In [1]:
import pandas as pd
import csv
from collections import OrderedDict

In [2]:
outputFolder = 'gtfs/'

In [3]:
faresChartFile = 'fares_chart_pivoted.csv'

## unpivoting function
defining the function below:

In [15]:
def csvunpivot(filename, keepcols=['origin_id'], var_header='destination_id', value_header='fare_id', sortby=['origin_id','destination_id','fare_id']):
    fares_pivoted = pd.read_csv(filename, encoding='utf8')
    
    print(fares_pivoted.sample(4))
    
    firstCol = keepcols[0]
    if list(fares_pivoted)[0] != firstCol:
        fares_pivoted.rename(columns ={list(fares_pivoted)[0]: 'origin_id'}, inplace=True)
        # rename first column, regardless of its orginal value or blank. from https://stackoverflow.com/a/26336314/4355695

    
    print( 'Loading and unpivoting',filename)
    fares_unpivoted = pd.melt(fares_pivoted, id_vars=keepcols, var_name=var_header, value_name=value_header).sort_values(by=sortby)

    # drop all rows having NaN values. from https://stackoverflow.com/a/13434501/4355695
    fares_unpivoted_clean = fares_unpivoted.dropna()
    
    # fares_dict = fares_unpivoted_clean.to_dict('records')
    return fares_unpivoted_clean

## unpivot fares chart table to get fare_rules

In [16]:
fares_rules_df = csvunpivot(faresChartFile, ['origin_id'], 'destination_id', 'fare_id', ['origin_id','destination_id','fare_id'])

   Unnamed: 0  MYP  JNT  KPH  KUK  BLR  MSP  BTN  ERA  ESI ...   NGRI  HSG  \
24        CHP   55   55   55   50   50   50   45   45   45 ...     60   60   
36        PAR   45   45   40   40   40   35   35   30   30 ...     35   30   
30       NGRI   55   55   50   50   50   50   45   45   45 ...     10   10   
16        NAM   45   45   45   40   40   40   40   35   30 ...     50   50   

    TAR  MET  SEC  PRG  PAR  RSP  PRN  BEG  
24   55   55   50   50   50   50   45   45  
36   25   25   15   10   10   10   15   15  
30   15   15   25   30   35   35   40   40  
16   45   45   40   40   40   40   35   30  

[4 rows x 41 columns]
Loading and unpivoting fares_chart_pivoted.csv


In [7]:
fares_rules_df.sample(20)

origin_id destination_id  fare_id
410        AME            AME       10
610        AME            ASM       25
1570       AME            BEG       10
170        AME            BLR       25
250        AME            BTN       25
970        AME            CHP       40
930        AME            DSN       40
290        AME            ERA       15
330        AME            ESI       10
690        AME            GAB       30
1250       AME            HSG       40
490        AME            IRM       15
50         AME            JNT       35
530        AME            KHA       15
90         AME            KPH       35
130        AME            KUK       30
1050       AME            LBN       45
570        AME            LKP       25
1330       AME            MET       35
770        AME            MGB       35
810        AME            MKL       35
890        AME            MSB       40
210        AME            MSP       25
10         AME            MYP       40
1090       AME            NAG       45
650        AME            NAM       25
850        AME            NEM       40
1210       AME           NGRI       40
730        AME            OMC       30
1450       AME            PAR       25
...        ...            ...      ...
1265       VOM            HSG       60
505        VOM            IRM       40
65         VOM            JNT       55
545        VOM            KHA       40
105        VOM            KPH       55
145        VOM            KUK       50
1065       VOM            LBN       10
585        VOM            LKP       40
1345       VOM            MET       55
785        VOM            MGB       30
825        VOM            MKL       25
905        VOM            MSB       15
225        VOM            MSP       50
25         VOM            MYP       60
1105       VOM            NAG       60
665        VOM            NAM       35
865        VOM            NEM       25
1225       VOM           NGRI       60
745        VOM            OMC       30
1465       VOM            PAR       50
1425       VOM            PRG       50
1545       VOM            PRN       50
465        VOM            PUN       45
1505       VOM            RSP       50
1385       VOM            SEC       55
385        VOM            SRN       45
1185       VOM            STD       60
1305       VOM            TAR       60
1145       VOM            UPL       60
1025       VOM            VOM       10

[1600 rows x 3 columns]

## generate fare_ids from unique numbers in fare_rules

In [8]:
farePrices = list(fares_rules_df.fare_id.unique())
farePrices.sort()
farePrices

[10, 15, 25, 30, 35, 40, 45, 50, 55, 60]

In [9]:
faresCollector = []
replaceDict = {}
for n, price in enumerate(farePrices):
    attrRow = OrderedDict({
        'fare_id': 'F' + str(n+1),
        'price': price,
        'currency_type': 'INR',
        'payment_method': 0,
        'transfers': '',
        'agency_id': 'HMRL'
    })
    faresCollector.append(attrRow)
    # while doing this, also create a substitution dict that will replace the prices for the fare id's in fare_rules table
    replaceDict[attrRow['price']] = attrRow['fare_id']

In [10]:
fareAttributesDF = pd.DataFrame(faresCollector)
fareAttributesDF

fare_id  price currency_type  payment_method transfers agency_id
0      F1     10           INR               0                HMRL
1      F2     15           INR               0                HMRL
2      F3     25           INR               0                HMRL
3      F4     30           INR               0                HMRL
4      F5     35           INR               0                HMRL
5      F6     40           INR               0                HMRL
6      F7     45           INR               0                HMRL
7      F8     50           INR               0                HMRL
8      F9     55           INR               0                HMRL
9     F10     60           INR               0                HMRL

## replace numbers in fare_rules table with id's

In [11]:
replaceDict

{10: 'F1',
 15: 'F2',
 25: 'F3',
 30: 'F4',
 35: 'F5',
 40: 'F6',
 45: 'F7',
 50: 'F8',
 55: 'F9',
 60: 'F10'}

In [12]:
fares_rules_df['fare_id'] = fares_rules_df['fare_id'].replace(to_replace=replaceDict)

In [13]:
fares_rules_df.sample(20)

origin_id destination_id fare_id
410        AME            AME      F1
610        AME            ASM      F3
1570       AME            BEG      F1
170        AME            BLR      F3
250        AME            BTN      F3
970        AME            CHP      F6
930        AME            DSN      F6
290        AME            ERA      F2
330        AME            ESI      F1
690        AME            GAB      F4
1250       AME            HSG      F6
490        AME            IRM      F2
50         AME            JNT      F5
530        AME            KHA      F2
90         AME            KPH      F5
130        AME            KUK      F4
1050       AME            LBN      F7
570        AME            LKP      F3
1330       AME            MET      F5
770        AME            MGB      F5
810        AME            MKL      F5
890        AME            MSB      F6
210        AME            MSP      F3
10         AME            MYP      F6
1090       AME            NAG      F7
650        AME            NAM      F3
850        AME            NEM      F6
1210       AME           NGRI      F6
730        AME            OMC      F4
1450       AME            PAR      F3
...        ...            ...     ...
1265       VOM            HSG     F10
505        VOM            IRM      F6
65         VOM            JNT      F9
545        VOM            KHA      F6
105        VOM            KPH      F9
145        VOM            KUK      F8
1065       VOM            LBN      F1
585        VOM            LKP      F6
1345       VOM            MET      F9
785        VOM            MGB      F4
825        VOM            MKL      F3
905        VOM            MSB      F2
225        VOM            MSP      F8
25         VOM            MYP     F10
1105       VOM            NAG     F10
665        VOM            NAM      F5
865        VOM            NEM      F3
1225       VOM           NGRI     F10
745        VOM            OMC      F4
1465       VOM            PAR      F8
1425       VOM            PRG      F8
1545       VOM            PRN      F8
465        VOM            PUN      F7
1505       VOM            RSP      F8
1385       VOM            SEC      F9
385        VOM            SRN      F7
1185       VOM            STD     F10
1305       VOM            TAR     F10
1145       VOM            UPL     F10
1025       VOM            VOM      F1

[1600 rows x 3 columns]

## write gtfs files

In [14]:
fares_rules_df.to_csv(outputFolder + 'fare_rules.txt', index=False)
fareAttributesDF.to_csv(outputFolder + 'fare_attributes.txt', index=False)